#### 1. Introduction

In this project, we will be exploring the following questions:
 - Is there a model that we can use to predict if a flight will get cancelled or delayed prior to its departure?
 - If the flight gets delayed, could a model predict how long it will take to take off?

#### 2. Data

##### 2.1. Data description

We will use airline performance data from the Office of Airline Information at the US Bureau of Transportation Statistics. 

The dataset contains information regarding non-stop domestic flight operated by certified US carriers that account for at least one percent of domestic scheduled passenger revenues. Data is reported directly from carriers and is available on a monthly basis from October 1987 to September 2020. The dataset is composed of 110 fields and a total of 196,156,313 records. The dataset includes information of scheduled and actual departure and arrival times, canceled and diverted flights, causes of delay and cancellation, airtime, non-stop distance, among other variables. 

A CSV file containing the data for each of the available months can be downloaded directly from the US Bureau of Transportation Statistics' website. For more information regarding the entire dataset, including the data directory can be found in the following link.  

 - https://www.transtats.bts.gov/TableInfo.asp

For this project, we will restrict our analysis to January 2019. Initially, we wanted to focus on the 5-year period of January 2015 to December 2019. However, given the size of the data and the cluster storage capability of Databricks Community Editions, we were unable to upload all the required files and the processing time was too long. We tried to reduce the sample to the year od 2019, but the data was still to big to work with. At the end, we decided to reduce our sample to include only data for January 2019. The code is written so that new months of 2019 can be easily added to the analysis.

First, we load the required packages:

In [0]:
#load requiered packages
import pandas as pd
import numpy as np

from functools import reduce
from pyspark.sql import DataFrame
from pyspark.sql.types import *
from pyspark.sql import functions

then, we read the data for our period of interest.

In [0]:
#load the data
frames = []
for month in range(1):
  #file location and type
  file_location = "/FileStore/tables/On_Time_Reporting_Carrier_On_Time_Performance__1987_present__2019_1.csv".format(month)
  file_type = "csv"

  #CSV options
  infer_schema = "true"
  first_row_is_header = "true"
  delimiter = ","

  #the applied options are for CSV files. For other file types, these will be ignored.
  df = spark.read.format(file_type) \
    .option("inferSchema", infer_schema) \
    .option("header", first_row_is_header) \
    .option("sep", delimiter) \
    .load(file_location)

  #display(df)
  frames.append(df)

#concatenate frames
data = reduce(DataFrame.unionAll, frames)

Now, we visualize the data and get an calculate its size.

In [0]:
#visualize the data
display(data)

Year Quarter Month DayofMonth DayOfWeek FlightDate Reporting_Airline DOT_ID_Reporting_Airline IATA_CODE_Reporting_Airline Tail_Number Flight_Number_Reporting_Airline OriginAirportID OriginAirportSeqID OriginCityMarketID Origin OriginCityName OriginState OriginStateFips OriginStateName OriginWac DestAirportID DestAirportSeqID DestCityMarketID Dest DestCityName DestState DestStateFips DestStateName DestWac CRSDepTime DepTime DepDelay DepDelayMinutes DepDel15 DepartureDelayGroups DepTimeBlk TaxiOut WheelsOff WheelsOn TaxiIn CRSArrTime ArrTime ArrDelay ArrDelayMinutes ArrDel15 ArrivalDelayGroups ArrTimeBlk Cancelled CancellationCode Diverted CRSElapsedTime ActualElapsedTime AirTime Flights Distance DistanceGroup CarrierDelay WeatherDelay NASDelay SecurityDelay LateAircraftDelay FirstDepTime TotalAddGTime LongestAddGTime DivAirportLandings DivReachedDest DivActualElapsedTime DivArrDelay DivDistance Div1Airport Div1AirportID Div1AirportSeqID Div1WheelsOn Div1TotalGTime Div1LongestGTime Div1WheelsOff Div1TailNum Div2Airport Div2AirportID Div2AirportSeqID Div2WheelsOn Div2TotalGTime Div2LongestGTime Div2WheelsOff Div2TailNum Div3Airport Div3AirportID Div3AirportSeqID Div3WheelsOn Div3TotalGTime Div3LongestGTime Div3WheelsOff Div3TailNum Div4Airport Div4AirportID Div4AirportSeqID Div4WheelsOn Div4TotalGTime Div4LongestGTime Div4WheelsOff Div4TailNum Div5Airport Div5AirportID Div5AirportSeqID Div5WheelsOn Div5TotalGTime Div5LongestGTime Div5WheelsOff Div5TailNum _c109 2019 1 1 4 5 2019-01-04 OO 20304 OO N945SW 5657 14698 1469802 34236 SBP San Luis Obispo, CA CA 6 California 91 14771 1477104 32457 SFO San Francisco, CA CA 6 California 91 1400 1353 -7.0 0.0 0.0 -1 1400-1459 9.0 1402 1439 5.0 1510 1444 -26.0 0.0 0.0 -2 1500-1559 0.0 null 0.0 70.0 51.0 37.0 1.0 190.0 1 null null null null null null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2019 1 1 4 5 2019-01-04 OO 20304 OO N932SW 5658 12266 1226603 31453 IAH Houston, TX TX 48 Texas 74 15919 1591904 31834 XNA Fayetteville, AR AR 5 Arkansas 71 935 930 -5.0 0.0 0.0 -1 0900-0959 27.0 957 1113 6.0 1118 1119 1.0 1.0 0.0 0 1100-1159 0.0 null 0.0 103.0 109.0 76.0 1.0 438.0 2 null null null null null null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2019 1 1 4 5 2019-01-04 OO 20304 OO N932SW 5658 14783 1478302 34783 SGF Springfield, MO MO 29 Missouri 64 12266 1226603 31453 IAH Houston, TX TX 48 Texas 74 643 637 -6.0 0.0 0.0 -1 0600-0659 17.0 654 822 16.0 855 838 -17.0 0.0 0.0 -2 0800-0859 0.0 null 0.0 132.0 121.0 88.0 1.0 513.0 3 null null null null null null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2019 1 1 4 5 2019-01-04 OO 20304 OO N916SW 5659 12389 1238902 32389 ISN Williston, ND ND 38 North Dakota 66 11292 1129202 30325 DEN Denver, CO CO 8 Colorado 82 1335 1314 -21.0 0.0 0.0 -2 1300-1359 23.0 1337 1357 7.0 1433 1404 -29.0 0.0 0.0 -2 1400-1459 0.0 null 0.0 118.0 110.0 80.0 1.0 576.0 3 null null null null null null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2019 1 1 4 5 2019-01-04 OO 20304 OO N107SY 5660 13342 1334207 33342 MKE Milwaukee, WI WI 55 Wisconsin 45 11292 1129202 30325 DEN Denver, CO CO 8 Colorado 82 836 826 -10.0 0.0 0.0 -1 0800-0859 26.0 852 959 10.0 1040 1009 -31.0 0.0 0.0 -2 1000-1059 0.0 null 0.0 184.0 163.0 127.0 1.

Variable description of the dataset

Note: - All time is LOCAL time for departures and arrivals.

    If Single or 2-Digit Values are present for a Time Value, they represent 00:MM (e.g. 3 represents 00:03 or 12:03 AM).

YEAR - Year

QUARTER - 1: Jan-Mar, 2: Apr-Jun, 3: Jul-Sep, 4: Oct-Dec

MONTH - Month of Year

DAY_OF_MONTH - Date of Month

DAY_OF_WEEK - Day of Week (1: Monday, 7: Sunday)

FL_DATE - Full flight date (M/DD/YYYY)

MKT_CARRIER_FL_NUM - Flight Number

TAIL_NUM - Aircraft Tail Number (Usually starts with 'N')

ORIGIN - Flight Departure 3-Letter Airport Abbreviation

ORIGIN_CITY_NAME - Flight Departure City, State Names

ORIGIN_STATE_ABR - Flight Departure 2-Letter State Abbreviation

ORIGIN_STATE_NM - Flight Departure State Name

DEST - Flight Arrival 3-Letter Airport Abbreviation

DEST_CITY_NAME - Flight Arrival City, State Names

DEST_STATE_ABR - Flight Arrival 2-Letter State Abbreviation

DEST_STATE_NM - Flight Arrival State Name

CRS_DEP_TIME - Scheduled Departure Time (HHMM) (Single or 2-Digit Values Represent 00:MM, e.g. 3 represents 00:03 or 12:03 AM)

DEP_TIME - Actual Departure Time (HHMM)

DEP_DELAY - Departure Delay (Difference Between Actual Departure Time and Scheduled Departure Time in Minutes)

DEP_DELAY_NEW - Departure Delay Ignoring Early Departures (Listed as 0)

DEP_DEL15 - Departure Delay Greater Than 15 Minutes (0: Not Greater Than 15, 1: Greater Than 15)

DEP_DELAY_GROUP - Departure Delay in Number of 15-minute increments Rounded Down (e.g. Early Departure (< 0) is a value of -1, 30 or 42 minutes is a value of 2)

DEP_TIME_BLK - Scheduled Departure Time in Hourly Block (HHMM)

TAXI_OUT - Time between Airplane Taxi from Gate and Takeoff (WHEELS_OFF) Time (in Minutes)

WHEELS_OFF - Time of Airplane Takeoff (HHMM)

WHEELS_ON - Time of Airplane Landing (HHMM)

TAXI_IN - Time between Airplane Taxi to Gate and Landing (WHEELS_ON) Time (in Minutes)

CRS_ARR_TIME - Scheduled Arrival Time (HHMM) (Single or 2-Digit Values Represent 00:MM, e.g. 3 represents 00:03 or 12:03 AM)

ARR_TIME - Actual Arrival Time (HHMM)

ARR_DELAY - Arrival Delay (Difference Between Actual Arrival Time and Scheduled Arrival Time in Minutes)

ARR_DELAY_NEW - Arrival Delay Ignoring Early Arrivals (Listed as 0)

ARR_DEL15 - Arrival Delay Greater Than 15 Minutes (0: Not Greater Than 15, 1: Greater Than 15)

ARR_DELAY_GROUP - Arrival Delay in Number of 15-minute increments Rounded Down (e.g. Early Arrival (< 0) is a value of -1, 30 or 42 minutes is a value of 2)

ARR_TIME_BLK - Scheduled Arrival Time in Hourly Block (HHMM)

CANCELLED - 0: Flight Not Cancelled, 1: Flight Cancelled

CANCELLATION_CODE - Reason for Cancellation - if Cancelled, Letter Present (A: Carrier, B: Weather, C: National Aviation System, D: Security)

CRS_ELAPSED_TIME - Scheduled Total Flight Time (in Minutes)

ACTUAL_ELAPSED_TIME - Actual Total Elapsed Flight Time (in Minutes)

AIR_TIME - Actual Total Elapsed Time Airplane in the Air (in Minutes)

DISTANCE - Distance Between Departure and Arrival Airports (in Miles)

DISTANCE_GROUP - Distance Between Departure and Arrival Airports in Number of 250-Mile increments Rounded Down (e.g. 400 miles is a value of 1)

CARRIER_DELAY - Carrier Delay (in Minutes)

WEATHER_DELAY - Weather Delay (in Minutes)

NAS_DELAY - National Aviation System Delay (in Minutes)

SECURITY_DELAY - Security Delay (in Minutes)

LATE_AIRCRAFT_DELAY - Late Aircraft Delay (in Minutes)

In [0]:
#display the data size
print('Dataframe dimensions: ('+ str(data.count())+','+str(len(data.columns))+')')

Dataframe dimensions: (583985,110)

Flight data for January 2019 contains 110 features for 583,985 domestic flights.

##### 2.2. Data cleaning

##### 2.2.1. Remove unnecessary variables and drop duplicate values
From the table in section 1, and from the data dictionary for the dataset, we know that there are many variables that are irrelevant for our analysis. In this section, we remove the set of variables that are either repeated or that do not determine if a flight gets delayed or cancelled. We hope that this will reduce the processing time as the data frame will be smaller.

In [0]:
#list of columns to keep
cols = ['Year','Quarter','Month','DayofMonth','DayofWeek','FlightDate',
       'Reporting_Airline','OriginAirportID','OriginState',
       'OriginCityName','DestAirportID','DestState','DestCityName'
       'CRSDepTime','DepTime','DepDelay','DepDelayMinutes','DepDel15',
       'TaxiOut','TaxiIn','CRSArrTime','ArrTime','ArrDelay',
       'ArrDelayMinutes','ArrDel15','Cancelled','CancellationCode',
       'AirTime','Flights','Distance','DistanceGroup',
       'CarrierDelay','WeatherDelay','NASDelay','SecurityDelay',
       'LateAircraftDelay']

for col in data.columns:
  if col not in cols:
    data = data.drop(col)

In [0]:
#count the number of original data rows
n1=data.count()
print('number of original data rows:', n1)
##count the number of data rows after deleting duplicated data
n2=data.dropDuplicates().count()
print('numer of data rows after deleting duplicated data:', n2)
n3 = n1-n2
print('number of duplicated data:', n3)

data= data.dropDuplicates()

number of original data rows: 583985
numer of data rows after deleting duplicated data: 583983
number of duplicated data: 2

Now, we get an overview of the dataset that we will be working on from now onwards.

In [0]:
#display the data size
print('Dataframe dimensions: ('+ str(data.count())+','+str(len(data.columns))+')')

Dataframe dimensions: (583983,33)

After removing a set of variables that we consider irrelevant for our analysis and removing duplicated rows, we are left with 33 columns and 583,983 rows. Now, we proceed to explore the type of data for each column. Now, we look at the schema of our dataset. It is important to always check the schema in order to make sure that all variables are converted into their proper datatypes, especially during dara cleaning.

In [0]:
# print schema
data.printSchema()

root
-- Year: integer (nullable = true)
-- Quarter: integer (nullable = true)
-- Month: integer (nullable = true)
-- DayofMonth: integer (nullable = true)
-- FlightDate: string (nullable = true)
-- Reporting_Airline: string (nullable = true)
-- OriginAirportID: integer (nullable = true)
-- OriginCityName: string (nullable = true)
-- OriginState: string (nullable = true)
-- DestAirportID: integer (nullable = true)
-- DestState: string (nullable = true)
-- DepTime: integer (nullable = true)
-- DepDelay: double (nullable = true)
-- DepDelayMinutes: double (nullable = true)
-- DepDel15: double (nullable = true)
-- TaxiOut: double (nullable = true)
-- TaxiIn: double (nullable = true)
-- CRSArrTime: integer (nullable = true)
-- ArrTime: integer (nullable = true)
-- ArrDelay: double (nullable = true)
-- ArrDelayMinutes: double (nullable = true)
-- ArrDel15: double (nullable = true)
-- Cancelled: double (nullable = true)
-- CancellationCode: string (nullable = true)
-- AirTime: double (nullable = true)
-- Flights: double (nullable = true)
-- Distance: double (nullable = true)
-- DistanceGroup: integer (nullable = true)
-- CarrierDelay: double (nullable = true)
-- WeatherDelay: double (nullable = true)
-- NASDelay: double (nullable = true)
-- SecurityDelay: double (nullable = true)
-- LateAircraftDelay: double (nullable = true)

From above, we can see that the inferred schema suggests that most of the data that we will be working with is of numeric type. However, there are some variables that are of string type. From the data directory we also know that some of the variables that we are dealing with refer to dates and times. We change the type of these variables in the next sub-section.

Next, we explore if our data has null or NA values.

In [0]:
#Spark wouldn't process the original datatpe of the column "FlightDate". Hence, had to convert the datatype to "double" to debug the error

In [0]:
data=data.withColumn('FlightDate',data['FlightDate'].cast("double"))

In [0]:
#check if there are missing values
from pyspark.sql.functions import isnan, when, count, col

#nan values
data.select([count(when(isnan(c), c)).alias(c) for c in data.columns]).show()

#null values
data.select([count(when(col(c).isNull(), c)).alias(c) for c in data.columns]).show()

+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+----------------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+
Year|Quarter|Month|DayofMonth|FlightDate|Reporting_Airline|OriginAirportID|OriginCityName|OriginState|DestAirportID|DestState|DepTime|DepDelay|DepDelayMinutes|DepDel15|TaxiOut|TaxiIn|CRSArrTime|ArrTime|ArrDelay|ArrDelayMinutes|ArrDel15|Cancelled|CancellationCode|AirTime|Flights|Distance|DistanceGroup|CarrierDelay|WeatherDelay|NASDelay|SecurityDelay|LateAircraftDelay|
+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+----------------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+
 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+----------------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+

+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+----------------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+
Year|Quarter|Month|DayofMonth|FlightDate|Reporting_Airline|OriginAirportID|OriginCityName|OriginState|DestAirportID|DestState|DepTime|DepDelay|DepDelayMinutes|DepDel15|TaxiOut|TaxiIn|CRSArrTime|ArrTime|ArrDelay|ArrDelayMinutes|ArrDel15|Cancelled|CancellationCode|AirTime|Flights|Distance|DistanceGroup|CarrierDelay|WeatherDelay|NASDelay|SecurityDelay|LateAircraftDelay|
+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+----------------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+
 0| 0| 0| 0| 583983| 0| 0| 0| 0| 0| 0| 16350| 16353| 16353| 16353| 16614| 17059| 0| 17059| 18020| 18020| 18020| 0| 567259| 18020| 0| 0| 0| 478761| 478761| 478761| 478761| 478761|
+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+----------------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+

In [0]:
#From the above, we could just see that the "CancellationCode" column has Null values of about 567,259. This accounts for over 97% percent of missing data. We shall delete this column. 

#In the case of these other columns namely "CarrierDelay", "WeatherDelay", "NASDelay", "SecurityDelay" and "LateAircraftDelay" where each of these columns have about 81% of their data missing, for the purpose of exploratory data analysis in this project, we shall be replacing the missing data for all these columns with "0". We may still be able to find interesting insights about these columns regardless.

In [0]:
column_to_drop1 = ["CancellationCode"]
data = data.drop(*column_to_drop1)

In [0]:
columns_to_replace = ["CarrierDelay", "WeatherDelay", "NASDelay", "SecurityDelay", "LateAircraftDelay" ]
data= data.na.fill(0,columns_to_replace)
display(data)

Year Quarter Month DayofMonth FlightDate Reporting_Airline OriginAirportID OriginCityName OriginState DestAirportID DestState DepTime DepDelay DepDelayMinutes DepDel15 TaxiOut TaxiIn CRSArrTime ArrTime ArrDelay ArrDelayMinutes ArrDel15 Cancelled AirTime Flights Distance DistanceGroup CarrierDelay WeatherDelay NASDelay SecurityDelay LateAircraftDelay 2019 1 1 4 null OO 10333 Alpena, MI MI 14150 MI 457 -7.0 0.0 0.0 16.0 4.0 604 542 -22.0 0.0 0.0 0.0 25.0 1.0 69.0 1 0.0 0.0 0.0 0.0 0.0 2019 1 1 4 null OO 14150 Pellston, MI MI 10333 MI 2231 -2.0 0.0 0.0 11.0 6.0 2336 2311 -25.0 0.0 0.0 0.0 23.0 1.0 69.0 1 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 14747 Seattle, WA WA 11638 CA 1927 -3.0 0.0 0.0 20.0 3.0 2141 2140 -1.0 0.0 0.0 0.0 110.0 1.0 748.0 3 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 13486 Missoula, MT MT 14869 UT 1427 -3.0 0.0 0.0 10.0 8.0 1614 1601 -13.0 0.0 0.0 0.0 76.0 1.0 436.0 2 0.0 0.0 0.0 0.0 0.0 2019 1 1 4 null OO 14869 Salt Lake City, UT UT 10918 UT 759 -11.0 0.0 0.0 21.0 2.0 905 859 -6.0 0.0 0.0 0.0 37.0 1.0 221.0 1 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 10372 Aspen, CO CO 12892 CA 1344 51.0 51.0 1.0 44.0 6.0 1422 1537 75.0 75.0 1.0 0.0 123.0 1.0 737.0 3 13.0 0.0 24.0 0.0 38.0 2019 1 1 5 null OO 11298 Dallas/Fort Worth, TX TX 13061 TX 1329 -5.0 0.0 0.0 18.0 3.0 1505 1451 -14.0 0.0 0.0 0.0 61.0 1.0 396.0 2 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 15412 Knoxville, TN TN 13930 IL 554 -7.0 0.0 0.0 15.0 6.0 659 635 -24.0 0.0 0.0 0.0 80.0 1.0 475.0 2 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 14107 Phoenix, AZ AZ 11638 CA 2124 9.0 9.0 0.0 25.0 9.0 2159 2218 19.0 19.0 1.0 0.0 80.0 1.0 493.0 2 9.0 0.0 10.0 0.0 0.0 2019 1 1 5 null OO 11298 Dallas/Fort Worth, TX TX 10372 CO 836 -9.0 0.0 0.0 21.0 4.0 1028 1035 7.0 7.0 0.0 0.0 154.0 1.0 701.0 3 0.0 0.0 0.0 0.0 0.0 2019 1 1 4 null OO 10739 Brainerd, MN MN 13487 MN 1544 -11.0 0.0 0.0 11.0 7.0 1705 1630 -35.0 0.0 0.0 0.0 28.0 1.0 114.0 1 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 13198 Kansas City, MO MO 14057 OR 1354 -1.0 0.0 0.0 13.0 4.0 1605 1556 -9.0 0.0 0.0 0.0 225.0 1.0 1482.0 6 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 14679 San Diego, CA CA 14831 CA 2046 -4.0 0.0 0.0 27.0 4.0 2219 2223 4.0 4.0 0.0 0.0 66.0 1.0 417.0 2 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 14908 Santa Ana, CA CA 14831 CA 1309 -1.0 0.0 0.0 10.0 4.0 1432 1422 -10.0 0.0 0.0 0.0 59.0 1.0 342.0 2 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 10713 Boise, ID ID 14679 CA 811 1.0 1.0 0.0 20.0 3.0 936 950 14.0 14.0 0.0 0.0 136.0 1.0 749.0 3 0.0 0.0 0.0 0.0 0.0 2019 1 1 4 null OO 13476 Monterey, CA CA 11292 CO 1255 -10.0 0.0 0.0 16.0 7.0 1646 1619 -27.0 0.0 0.0 0.0 121.0 1.0 959.0 4 0.0 0.0 0.0 0.0 0.0 2019 1 1 4 null OO 11292 Denver, CO CO 14262 CA 1911 6.0 6.0 0.0 24.0 8.0 2030 2029 -1.0 0.0 0.0 0.0 106.0 1.0 776.0 4 0.0 0.0 0.0 0.0 0.0 2019 1 1 4 null OO 11013 Sault Ste. Marie, MI MI 11433 MI 1533 -10.0 0.0 0.0 21.0 11.0 1710 1649 -21.0 0.0 0.0 0.0 44.0 1.0 284.0 2 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 11057 Charlotte, NC NC 13342 WI 1002 817.0 817.0 1.0 22.0 3.0 2141 1123 822.0 822.0 1.0 0.0 116.0 1.0 651.0 3 817.0 0.0 5.0 0.0 0.0 2019 1 1 5 null OO 14893 Sacramento, CA CA 14057 OR 1017 52.0 52.0 1.0 12.0 3.0 1109 1138 29.0 29.0 1.0 0.0 66.0 1.0 479.0 2 0.0 0.0 0.0 0.0 29.0 2019 1 1 4 null OO 13476 Monterey, CA CA 12892 CA 1631 -9.0 0.0 0.0 21.0 16.0 1811 1803 -8.0 0.0 0.0 0.0 55.0 1.0 266.0 2 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 11298 Dallas/Fort Worth, TX TX 11140 TX 2038 -5.0 0.0 0.0 28.0 5.0 2219 2201 -18.0 0.0 0.0 0.0 50.0 1.0 354.0 2 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 14109 Hattiesburg/Laurel, MS MS 13241 MS 623 38.0 38.0 1.0 16.0 5.0 623 712 49.0 49.0 1.0 0.0 28.0 1.0 69.0 1 38.0 0.0 11.0 0.0 0.0 2019 1 1 5 null OO 13487 Minneapolis, MN MN 13871 NE 1022 -3.0 0.0 0.0 20.0 3.0 1153 1132 -21.0 0.0 0.0 0.0 47.0 1.0 282.0 2 0.0 0.0 0.0 0.0 0.0 2019 1 1 4 null OO 11433 Detroit, MI MI 12397 NY 1532 -8.0 0.0 0.0 14.0 4.0 1713 1637 -36.0 0.0 0.0 0.0 47.0 1.0 353.0 2 0.0 0.0 0.0 0.0 0.0 2019 1 1 5 null OO 11775 Sioux Falls, SD SD 139

In [0]:
#check if there are missing values
from pyspark.sql.functions import isnan, when, count, col

#nan values
data.select([count(when(isnan(c), c)).alias(c) for c in data.columns]).show()

#null values
data.select([count(when(col(c).isNull(), c)).alias(c) for c in data.columns]).show()

+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+
Year|Quarter|Month|DayofMonth|FlightDate|Reporting_Airline|OriginAirportID|OriginCityName|OriginState|DestAirportID|DestState|DepTime|DepDelay|DepDelayMinutes|DepDel15|TaxiOut|TaxiIn|CRSArrTime|ArrTime|ArrDelay|ArrDelayMinutes|ArrDel15|Cancelled|AirTime|Flights|Distance|DistanceGroup|CarrierDelay|WeatherDelay|NASDelay|SecurityDelay|LateAircraftDelay|
+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+
 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+

+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+
Year|Quarter|Month|DayofMonth|FlightDate|Reporting_Airline|OriginAirportID|OriginCityName|OriginState|DestAirportID|DestState|DepTime|DepDelay|DepDelayMinutes|DepDel15|TaxiOut|TaxiIn|CRSArrTime|ArrTime|ArrDelay|ArrDelayMinutes|ArrDel15|Cancelled|AirTime|Flights|Distance|DistanceGroup|CarrierDelay|WeatherDelay|NASDelay|SecurityDelay|LateAircraftDelay|
+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+
 0| 0| 0| 0| 583983| 0| 0| 0| 0| 0| 0| 16350| 16353| 16353| 16353| 16614| 17059| 0| 17059| 18020| 18020| 18020| 0| 18020| 0| 0| 0| 0| 0| 0| 0| 0|
+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+

##### 2.2.2. Handling missing values

After analyzing the data, we can see that our dataset does not contain any NA values. However, some of the variables have a large number of null values, meaning that a large set of information is missing. Rather than eliminating the rows that show missing values or removing the columns with a large share of missing values from our set of possible explanatory variables, we replace the missing data with statistical estimates. In this case, we will be using the mean as the imputation value.

In [0]:
#calculate the mean value for each variable
meanDepTime = data.groupBy().avg("DepTime").take(1)[0][0]
print('mean DepTime:', meanDepTime)

meanDepDelay = data.groupBy().avg("DepDelay").take(1)[0][0]
print('mean DepDelay:', meanDepDelay)

meanDepDelayMinutes = data.groupBy().avg("DepDelayMinutes").take(1)[0][0]
print('mean DepDelayMinutes:', meanDepDelayMinutes)

meanDepDel15 = data.groupBy().avg("DepDel15").take(1)[0][0]
print('mean DepDel15:', meanDepDel15)

meanTaxiOut = data.groupBy().avg("TaxiOut").take(1)[0][0]
print('mean TaxiOut:', meanTaxiOut)

meanTaxiIn = data.groupBy().avg("TaxiIn").take(1)[0][0]
print('mean TaxiIn:', meanTaxiIn)

meanArrTime = data.groupBy().avg("ArrTime").take(1)[0][0]
print('mean ArrTime:', meanArrTime)

meanArrDelay = data.groupBy().avg("ArrDelay").take(1)[0][0]
print('mean ArrDelay:', meanArrDelay)

meanArrDelayMinutes = data.groupBy().avg("ArrDelayMinutes").take(1)[0][0]
print('mean ArrDelayMinutes:', meanArrDelayMinutes)

meanArrDel15 = data.groupBy().avg("ArrDel15").take(1)[0][0]
print('mean ArrDel15:', meanArrDel15)

meanAirTime = data.groupBy().avg("AirTime").take(1)[0][0]
print('mean AirTime:', meanAirTime)

#drop duplicated data and fill missing data with mean value
data=data.fillna({'DepTime': meanDepTime, 'DepDelay': meanDepDelay, 'DepDelayMinutes': meanDepDelayMinutes, 'DepDel15': meanDepDel15, 'TaxiOut': meanTaxiOut, 'TaxiIn': meanTaxiIn, 'ArrTime': meanArrTime, 'ArrDelay': meanArrDelay, 'ArrDelayMinutes': meanArrDelayMinutes,'ArrDel15': meanArrDel15, 'AirTime': meanAirTime,})

mean DepTime: 1331.9578142919809
mean DepDelay: 9.766090587178267
mean DepDelayMinutes: 13.25822630939168
mean DepDel15: 0.17428078149498794
mean TaxiOut: 18.331121368985617
mean TaxiIn: 7.59773267669035
mean ArrTime: 1484.3159206525038
mean ArrDelay: 4.257506232739596
mean ArrDelayMinutes: 13.65453925433288
mean ArrDel15: 0.18591674720785634
mean AirTime: 112.69446059194682

In [0]:
#Let's verify that we have tackled all Null values in our dataset

data.select([count(when(col(c).isNull(), c)).alias(c) for c in data.columns]).show()

+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+
Year|Quarter|Month|DayofMonth|FlightDate|Reporting_Airline|OriginAirportID|OriginCityName|OriginState|DestAirportID|DestState|DepTime|DepDelay|DepDelayMinutes|DepDel15|TaxiOut|TaxiIn|CRSArrTime|ArrTime|ArrDelay|ArrDelayMinutes|ArrDel15|Cancelled|AirTime|Flights|Distance|DistanceGroup|CarrierDelay|WeatherDelay|NASDelay|SecurityDelay|LateAircraftDelay|
+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+
 0| 0| 0| 0| 583983| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
+----+-------+-----+----------+----------+-----------------+---------------+--------------+-----------+-------------+---------+-------+--------+---------------+--------+-------+------+----------+-------+--------+---------------+--------+---------+-------+-------+--------+-------------+------------+------------+--------+-------------+-----------------+

In [0]:
data.printSchema()

root
-- Year: integer (nullable = true)
-- Quarter: integer (nullable = true)
-- Month: integer (nullable = true)
-- DayofMonth: integer (nullable = true)
-- FlightDate: double (nullable = true)
-- Reporting_Airline: string (nullable = true)
-- OriginAirportID: integer (nullable = true)
-- OriginCityName: string (nullable = true)
-- OriginState: string (nullable = true)
-- DestAirportID: integer (nullable = true)
-- DestState: string (nullable = true)
-- DepTime: integer (nullable = true)
-- DepDelay: double (nullable = false)
-- DepDelayMinutes: double (nullable = false)
-- DepDel15: double (nullable = false)
-- TaxiOut: double (nullable = false)
-- TaxiIn: double (nullable = false)
-- CRSArrTime: integer (nullable = true)
-- ArrTime: integer (nullable = true)
-- ArrDelay: double (nullable = false)
-- ArrDelayMinutes: double (nullable = false)
-- ArrDel15: double (nullable = false)
-- Cancelled: double (nullable = true)
-- AirTime: double (nullable = false)
-- Flights: double (nullable = true)
-- Distance: double (nullable = true)
-- DistanceGroup: integer (nullable = true)
-- CarrierDelay: double (nullable = false)
-- WeatherDelay: double (nullable = false)
-- NASDelay: double (nullable = false)
-- SecurityDelay: double (nullable = false)
-- LateAircraftDelay: double (nullable = false)

VOILA!!! We have successfully cleaned up our data. We have our cleaned dataframe to work with

##### 2.2.3. Change data types for dates
Above we mentioned that some of the variables that we are dealing with refer to dates. However, the schema assumed those variables were of string type. In this section, we change the data types for the flight date variable.

In [0]:
# change date type of 'FlightDate' from double to date
#data = data.withColumn('FlightDate',data['FlightDate'].cast(DateType()))

##### 2.3. Data exploration

In this section, we explore our data and try to look for interesting correlations among our variables and our variable of interest.

In [0]:
# Create a temporary view or table out of the above dataframe..
temp_table_name = "flightdata"

data.createOrReplaceTempView(temp_table_name)

##### 2.3.1. Cancelled Flights in Jan 2019

In [0]:
%sql /*the deafault notebook is python, but if you have to run any other notebook, follow this syntax

/* Query the created temp table in a SQL cell */

select count(*) as Cancelled from flightdata where Cancelled=1

Cancelled 16724

Out of a total of 583,983 flights that were scheduled for January 2019, 16,724 were cancelled. This corresponds to 2.86% of flights.

##### 2.3.2. Cities with the most Cancellations

Let's look at what cities had the most cancellations

In [0]:
%sql select OriginCityName, count(Cancelled) as Cancelled from flightdata where Cancelled=1 group by OriginCityName order by Cancelled DESC

OriginCityName Cancelled Chicago, IL 3595 Washington, DC 779 New York, NY 704 Boston, MA 702 San Francisco, CA 574 Detroit, MI 388 Atlanta, GA 313 Baltimore, MD 307 Charlotte, NC 289 Dallas/Fort Worth, TX 288 Los Angeles, CA 263 St. Louis, MO 257 Newark, NJ 241 Minneapolis, MN 224 Denver, CO 221 Cleveland, OH 194 Philadelphia, PA 188 Phoenix, AZ 187 Nashville, TN 185 Orlando, FL 184 Indianapolis, IN 178 Buffalo, NY 171 Houston, TX 170 Milwaukee, WI 168 Las Vegas, NV 153 Kansas City, MO 150 Columbus, OH 136 Fort Lauderdale, FL 127 Tampa, FL 120 Grand Rapids, MI 114 Cincinnati, OH 113 San Diego, CA 113 Fort Myers, FL 113 Pittsburgh, PA 111 Hartford, CT 107 Dallas, TX 98 Aspen, CO 97 Raleigh/Durham, NC 92 Rochester, NY 86 Burbank, CA 83 Omaha, NE 83 Syracuse, NY 81 San Jose, CA 80 Albany, NY 78 Seattle, WA 75 Richmond, VA 74 Des Moines, IA 66 Miami, FL 66 Oakland, CA 62 Burlington, VT 61 Providence, RI 61 Austin, TX 60 Cedar Rapids/Iowa City, IA 60 White Plains, NY 60 Jacksonville, FL 60 Oklahoma City, OK 59 Portland, OR 57 West Palm Beach/Palm Beach, FL 54 South Bend, IN 53 New Orleans, LA 53 Norfolk, VA 52 Salt Lake City, UT 51 Sacramento, CA 51 Sun Valley/Hailey/Ketchum, ID 46 Memphis, TN 45 Madison, WI 45 Manchester, NH 43 Greensboro/High Point, NC 43 San Antonio, TX 43 Louisville, KY 42 Chattanooga, TN 41 Palm Springs, CA 39 Dayton, OH 38 Charleston, SC 38 Lexington, KY 38 Moline, IL 37 Albuquerque, NM 37 Rochester, MN 37 Wichita, KS 36 Portland, ME 36 Sioux Falls, SD 36 Fayetteville, AR 35 Birmingham, AL 34 Greer, SC 34 Juneau, AK 33 Peoria, IL 33 Santa Ana, CA 33 Knoxville, TN 31 Fargo, ND 31 Savannah, GA 30 Ontario, CA 29 Fort Wayne, IN 29 Columbia, MO 29 Tulsa, OK 28 Green Bay, WI 28 Harrisburg, PA 26 Charlottesville, VA 26 Traverse City, MI 25 Asheville, NC 25 Flint, MI 23 Bloomington/Normal, IL 23 San Luis Obispo, CA 23 Little Rock, AR 22 Toledo, OH 22 Huntsville, AL 22 Eagle, CO 20 Akron, OH 20 Champaign/Urbana, IL 20 Santa Barbara, CA 19 Paducah, KY 19 Colorado Springs, CO 19 Mammoth Lakes, CA 19 Bend/Redmond, OR 19 Fresno, CA 19 Allentown/Bethlehem/Easton, PA 18 Lansing, MI 18 Tucson, AZ 18 Saginaw/Bay City/Midland, MI 18 Springfield, MO 17 Kalamazoo, MI 17 Reno, NV 17 Evansville, IN 17 Springfield, IL 16 Scranton/Wilkes-Barre, PA 16 Sioux City, IA 16 San Juan, PR 15 Spokane, WA 15 La Crosse, WI 15 Arcata/Eureka, CA 15 Mosinee, WI 15 Boise, ID 15 Dubuque, IA 15 Watertown, NY 15 Muskegon, MI 14 Bangor, ME 14 Medford, OR 14 Appleton, WI 14 Hancock/Houghton, MI 14 Sarasota/Bradenton, FL 14 Anchorage, AK 13 Manhattan/Ft. Riley, KS 13 Monterey, CA 13 Quincy, IL 13 State College, PA 13 Hays, KS 13 Pensacola, FL 13 Baton Rouge, LA 13 Eugene, OR 13 Jackson, WY 11 Hayden, CO 11 Redding, CA 11 Charleston/Dunbar, WV 10 Duluth, MN 10 Cape Girardeau, MO 10 Bismarck/Mandan, ND 10 Panama City, FL 10 Grand Forks, ND 10 Jackson/Vicksburg, MS 10 Salina, KS 9 El Paso, TX 9 Wilmington, NC 9 Eau Claire, WI 9 Jamestown, ND 9 Lewisburg, WV 9 Tallahassee, FL 8 Bozeman, MT 8 Long Beach, CA 8 Columbia, SC 8 Staunton, VA 8 Lawton/Fort Sill, OK 8 Petersburg, AK 7 Clarksburg/Fairmont, WV 7 Vernal, UT 7 Ketchikan, AK 7 Islip, NY 7 Waterloo, IA 7 Rapid City, SD 7 Binghamton, NY 7 Fairbanks, AK 7 Mobile, AL 7 Moab, UT 6 North Bend/Coos Bay, OR 6 St. Petersburg, FL 6 Amarillo, TX 6 Valparaiso, FL 6 Meridian, MS 6 Gulfport/Biloxi, MS 6 Wichita Falls, TX 6 Pellston, MI 6 Mission/McAllen/Edinburg, TX 6 Garden City, KS 5 Honolulu, HI 5 Santa Rosa, CA 5 Sanford, FL 5 Fayetteville, NC 5 Monroe, LA 5 Devils Lake, ND 5 Minot, ND 5 Yakutat, AK 5 Plattsburgh, NY 5 College Station/Bryan, TX 5 Kona, HI 5 Durango, CO 5 Santa Fe, NM 5 Worcester, MA 5 Shreveport, LA 5 Pasco/Kennewick/Richland, WA 4 Montrose/Delta, CO 4 Alpena, MI 4 Elko, NV 4 Kalispell, MT 4 Escanaba, MI 4 Bethel, AK 4 Midland/Odessa, TX 4 Lubbock, TX 4 Wrangell, AK 4 New Haven, CT 4 Flagstaff, AZ 4 Marquette, MI 4 Roanoke, VA 4 Hilton Head, SC 4 Tyler, TX 3 San Angelo, TX 3 Laredo, TX 3 New Bern

Chicago is no surprise given it is a very busy airport. However, chicago is actually the 3rd busiest airport. Atlanta is the most busy but is ranked 7th in the list above. Very curious. Windy city for a reason, maybe? We should now look into weather related incidents to maybe explain this.

source   https://en.wikipedia.org/wiki/List_of_the_busiest_airports_in_the_United_States

##### 2.3.3. Count of Departure Delays by OriginCityName

In [0]:
%sql select OriginCityName, count(DepDelay) as DepDelay from flightdata where DepDelay > 40 group by OriginCityName order by DepDelay DESC

OriginCityName DepDelay Chicago, IL 4497 New York, NY 3462 San Francisco, CA 1839 Dallas/Fort Worth, TX 1782 Atlanta, GA 1626 Washington, DC 1604 Denver, CO 1568 Newark, NJ 1560 Boston, MA 1495 Los Angeles, CA 1478 Houston, TX 1395 Detroit, MI 1302 Charlotte, NC 1205 Orlando, FL 970 Phoenix, AZ 958 Minneapolis, MN 957 Fort Lauderdale, FL 893 Las Vegas, NV 888 Salt Lake City, UT 664 Miami, FL 640 Philadelphia, PA 538 Baltimore, MD 530 Nashville, TN 507 San Diego, CA 507 Tampa, FL 496 Raleigh/Durham, NC 470 Seattle, WA 466 St. Louis, MO 451 Cleveland, OH 417 Fort Myers, FL 369 Cincinnati, OH 366 Columbus, OH 347 Pittsburgh, PA 335 West Palm Beach/Palm Beach, FL 326 Dallas, TX 310 Austin, TX 304 Indianapolis, IN 301 Kansas City, MO 300 New Orleans, LA 299 San Jose, CA 267 Portland, OR 260 San Juan, PR 246 Milwaukee, WI 244 Aspen, CO 230 Oakland, CA 208 Jacksonville, FL 206 Norfolk, VA 202 Grand Rapids, MI 199 Santa Ana, CA 194 Richmond, VA 191 Sacramento, CA 189 Buffalo, NY 185 Omaha, NE 172 Burbank, CA 164 Louisville, KY 162 Hartford, CT 159 San Antonio, TX 154 Oklahoma City, OK 153 Honolulu, HI 146 Syracuse, NY 134 Memphis, TN 128 Des Moines, IA 125 Burlington, VT 123 Rochester, NY 119 Tucson, AZ 119 Reno, NV 118 Palm Springs, CA 117 Madison, WI 114 White Plains, NY 112 Savannah, GA 112 Providence, RI 111 Charleston, SC 111 Greensboro/High Point, NC 110 Fayetteville, AR 107 Birmingham, AL 104 Knoxville, TN 102 Boise, ID 93 Eagle, CO 93 Fresno, CA 92 Albany, NY 92 Ontario, CA 90 Albuquerque, NM 87 Jackson, WY 85 Long Beach, CA 84 Greer, SC 80 Kahului, HI 79 Lexington, KY 78 Cedar Rapids/Iowa City, IA 77 El Paso, TX 77 South Bend, IN 77 Tulsa, OK 76 Sarasota/Bradenton, FL 72 Colorado Springs, CO 71 Fort Wayne, IN 70 Dayton, OH 68 Springfield, MO 66 Bozeman, MT 65 Baton Rouge, LA 62 Spokane, WA 60 Anchorage, AK 60 Medford, OR 60 Fargo, ND 59 Moline, IL 59 Asheville, NC 58 Sanford, FL 58 Sioux Falls, SD 58 Key West, FL 56 Portland, ME 56 Little Rock, AR 55 Santa Barbara, CA 55 Wichita, KS 54 Appleton, WI 54 Akron, OH 53 Eugene, OR 51 Myrtle Beach, SC 51 Kona, HI 51 San Luis Obispo, CA 50 Chattanooga, TN 49 Jackson/Vicksburg, MS 48 Charlottesville, VA 48 Pensacola, FL 47 Harrisburg, PA 45 Huntsville, AL 44 Bend/Redmond, OR 44 Islip, NY 44 Peoria, IL 44 Punta Gorda, FL 43 Lihue, HI 43 Green Bay, WI 42 Wilmington, NC 39 Midland/Odessa, TX 39 Columbia, SC 38 Shreveport, LA 38 Monterey, CA 37 Rapid City, SD 36 Charleston/Dunbar, WV 35 Rochester, MN 34 Mobile, AL 32 Champaign/Urbana, IL 31 Panama City, FL 31 Manchester, NH 31 Charlotte Amalie, VI 30 Traverse City, MI 30 Bangor, ME 30 Bismarck/Mandan, ND 29 Durango, CO 29 Hayden, CO 29 Mission/McAllen/Edinburg, TX 28 Allentown/Bethlehem/Easton, PA 28 Arcata/Eureka, CA 28 Trenton, NJ 28 Montrose/Delta, CO 26 Amarillo, TX 26 Valparaiso, FL 26 Duluth, MN 26 Lafayette, LA 26 Evansville, IN 25 Bloomington/Normal, IL 24 Newburgh/Poughkeepsie, NY 24 Meridian, MS 24 Columbia, MO 23 Flint, MI 23 Lansing, MI 23 Grand Forks, ND 22 Montgomery, AL 22 Juneau, AK 21 Harlingen/San Benito, TX 20 Aguadilla, PR 20 Roanoke, VA 20 Salina, KS 20 Fayetteville, NC 20 Pasco/Kennewick/Richland, WA 19 Lubbock, TX 19 Tallahassee, FL 19 Kalamazoo, MI 18 Saginaw/Bay City/Midland, MI 18 Manhattan/Ft. Riley, KS 17 Scranton/Wilkes-Barre, PA 17 Gainesville, FL 17 Gulfport/Biloxi, MS 17 Augusta, GA 17 Hays, KS 17 Minot, ND 16 Monroe, LA 16 St. Petersburg, FL 16 Corpus Christi, TX 16 Paducah, KY 16 Ketchikan, AK 16 Billings, MT 16 Mammoth Lakes, CA 15 Springfield, IL 15 Kalispell, MT 15 Marquette, MI 15 Atlantic City, NJ 14 Fairbanks, AK 14 Great Falls, MT 14 Worcester, MA 14 Grand Junction, CO 14 College Station/Bryan, TX 14 Bakersfield, CA 14 Redding, CA 13 Laredo, TX 13 Sun Valley/Hailey/Ketchum, ID 13 Killeen, TX 13 Flagstaff, AZ 12 Iron Mountain/Kingsfd, MI 12 Ithaca/Cortland, NY 12 Roswell, NM 12 Grand Island, NE 12 Cape Girardeau, MO 12 Mosinee, WI 12 Missoula, MT 12 Daytona Beach, FL 12 Santa Fe, NM 12 Twin Falls, I

This shows that Chicago,IL has the highest number of Departure Delay flights, seconded by New York, NY and San Francisco, CA

##### 2.3.4. Bucket Dataset for Cancelled and Non-Cancelled Flights

In [0]:
#We want to know how many cancelled and non cancelled flights are displayed in the dataset. 
display(data.groupBy('Cancelled').count())

Cancelled count 0.0 567259 1.0 16724

Its clearly seen that most of the flights are not cancelled in the month of January 2019. Just nearly 3% of flights were Cancelled.

##### 2.3.5. Count of Cancelled Flights by DayofMonth

In [0]:
%sql
select DayofMonth, Cancelled, count(*) from flightdata group by DayofMonth, Cancelled order by DayofMonth

DayofMonth Cancelled count(1) 1 1.0 141 1 0.0 17868 2 1.0 173 2 0.0 20211 3 1.0 134 3 0.0 19388 4 0.0 19495 4 1.0 71 5 1.0 129 5 0.0 16678 6 0.0 19153 6 1.0 295 7 0.0 19899 7 1.0 116 8 1.0 188 8 0.0 18626 9 0.0 19061 9 1.0 174 10 0.0 19797 10 1.0 183 11 1.0 219 11 0.0 19863 12 1.0 329 12 0.0 14986 13 0.0 17841 13 1.0 720 14 1.0 251 14 0.0 19690 15 0.0 18404 15 1.0 249 16 1.0 303 16 0.0 18796 17 0.0 19761 17 1.0 199 18 1.0 415 18 0.0 19594 19 0.0 13422 19 1.0 1513 20 1.0 1175 20 0.0 15700 21 1.0 599 21 0.0 18912 22 0.0 17519 22 1.0 1138 23 1.0 596 23 0.0 18503 24 1.0 421 24 0.0 19542 25 1.0 191 25 0.0 19850 26 0.0 15194 26 1.0 73 27 0.0 18371 27 1.0 204 28 0.0 18487 28 1.0 1447 29 1.0 1158 29 0.0 17504 30 0.0 16957 30 1.0 2145 31 0.0 18187 31 1.0 1775

The plot above shows that flights towards the early days of the month and between 25th-27th of Jan had lesser flight cancellations, with the highest number of cancellations recorded in Jan 30th & 31st. In other words, cancellations are less likely to occur between the first two weeks of the month

##### 2.3.6. Count of Departure Delays by DayofMonth

In [0]:
%sql select DayofMonth, count (DepDelay) from flightdata where DepDelay > 40 group by DayofMonth order by DayofMonth

DayofMonth count(DepDelay) 1 1710 2 2306 3 1455 4 1052 5 1317 6 1903 7 1357 8 911 9 873 10 1581 11 1288 12 856 13 1373 14 1380 15 1172 16 1060 17 1625 18 1823 19 1152 20 1528 21 2738 22 2200 23 2777 24 3318 25 2360 26 940 27 1329 28 1799 29 1192 30 1868 31 1942

We can see a slight decrease in the Departure Delays of flights in the first two weeks and then a spike between Jan 23rd-24th.
It seems higher percentage of delays occurs in the third week of the month.

##### 2.4. Data modeling

#####2.4.1 Indexing String data

Because some of the columns are Strings, we are not able to use them to do some types of machine learning on them. In order to use these columns, we must use a StringIndexer to convert thee columns into ints. Each unique string will be assigned an int value that will be used by the machine learning algorithms.

In [0]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.feature import StringIndexer

inputCols = ["Reporting_Airline", "OriginCityName", "OriginState", "DestState"]
outputCols = ["airlineIndex", "originCityIndex", "OriginStateIndex", "DestStateIndex"]
Indexer = StringIndexer(inputCols=inputCols, outputCols=outputCols)
indexedData = Indexer.fit(data).transform(data)

Now the columns we wish to use for making machine learning models is ready to be used.

#####2.4.2 Predicting likelihood of a Flight being delayed (Using Binomial Logistic Regression)

The first model we want to make is one that predicts the likelihood of a flight being delayed. We use Day of Month (though we only have one month of data), the Airline, the Origin Airport, Origin City, Origin State, Destination Airport, Destinataion State, Distance and Departure Time to predict whether a flight will be delayed. The rationale for using Day & Departure Time was that more flights may have been delayed on a specific day/time due to a common reason (such as weather, or airport difficulties). Specific Airlines may be more prone to delays, or specific airports/cities/states may be more prone to delays, hence why these datapoints were used. Distance may have had a factor, and thus was added.

In [0]:
delayLiklyFeatureCols = ["DayofMonth", "airlineIndex", "OriginAirportID", "originCityIndex", "OriginStateIndex", "DestAirportID", "DestStateIndex", "Distance", "DepTime"]

assembler = (VectorAssembler()
  .setInputCols(delayLiklyFeatureCols)
  .setOutputCol("delayLikelyFeatures"))

delayLikelyFinalPrep = assembler.transform(indexedData)

In our exisiting database we have columns that measure the length of delay (through various forms of measure), but for logisitc regression when need a binary column, one that indicates if a flight was delayed or not.

In [0]:
from pyspark.sql.functions import col,lit,when

delayLikelyFinalPrep = delayLikelyFinalPrep.withColumn("delayed?", when(col("DepDelayMinutes") > 0, lit(1)).otherwise(lit(0)))
display(delayLikelyFinalPrep)

Year Quarter Month DayofMonth FlightDate Reporting_Airline OriginAirportID OriginCityName OriginState DestAirportID DestState DepTime DepDelay DepDelayMinutes DepDel15 TaxiOut TaxiIn CRSArrTime ArrTime ArrDelay ArrDelayMinutes ArrDel15 Cancelled AirTime Flights Distance DistanceGroup CarrierDelay WeatherDelay NASDelay SecurityDelay LateAircraftDelay airlineIndex originCityIndex OriginStateIndex DestStateIndex delayLikelyFeatures delayed? 2019 1 1 4 null OO 10333 Alpena, MI MI 14150 MI 457 -7.0 0.0 0.0 16.0 4.0 604 542 -22.0 0.0 0.0 0.0 25.0 1.0 69.0 1 0.0 0.0 0.0 0.0 0.0 3.0 308.0 10.0 10.0 Map(vectorType -> dense, length -> 9, values -> List(4.0, 3.0, 10333.0, 308.0, 10.0, 14150.0, 10.0, 69.0, 457.0)) 0 2019 1 1 4 null OO 14150 Pellston, MI MI 10333 MI 2231 -2.0 0.0 0.0 11.0 6.0 2336 2311 -25.0 0.0 0.0 0.0 23.0 1.0 69.0 1 0.0 0.0 0.0 0.0 0.0 3.0 259.0 10.0 10.0 Map(vectorType -> dense, length -> 9, values -> List(4.0, 3.0, 14150.0, 259.0, 10.0, 10333.0, 10.0, 69.0, 2231.0)) 0 2019 1 1 5 null OO 14747 Seattle, WA WA 11638 CA 1927 -3.0 0.0 0.0 20.0 3.0 2141 2140 -1.0 0.0 0.0 0.0 110.0 1.0 748.0 3 0.0 0.0 0.0 0.0 0.0 3.0 17.0 15.0 0.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 14747.0, 17.0, 15.0, 11638.0, 0.0, 748.0, 1927.0)) 0 2019 1 1 5 null OO 13486 Missoula, MT MT 14869 UT 1427 -3.0 0.0 0.0 10.0 8.0 1614 1601 -13.0 0.0 0.0 0.0 76.0 1.0 436.0 2 0.0 0.0 0.0 0.0 0.0 3.0 177.0 39.0 19.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 13486.0, 177.0, 39.0, 14869.0, 19.0, 436.0, 1427.0)) 0 2019 1 1 5 null OO 14869 Salt Lake City, UT UT 10713 ID 830 0.0 0.0 0.0 35.0 3.0 1001 958 -3.0 0.0 0.0 0.0 50.0 1.0 290.0 2 0.0 0.0 0.0 0.0 0.0 3.0 18.0 19.0 37.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 14869.0, 18.0, 19.0, 10713.0, 37.0, 290.0, 830.0)) 0 2019 1 1 5 null OO 11292 Denver, CO CO 11468 NE 2007 -3.0 0.0 0.0 19.0 5.0 2225 2213 -12.0 0.0 0.0 0.0 42.0 1.0 305.0 2 0.0 0.0 0.0 0.0 0.0 3.0 6.0 8.0 34.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 11292.0, 6.0, 8.0, 11468.0, 34.0, 305.0, 2007.0)) 0 2019 1 1 5 null OO 13930 Chicago, IL IL 10599 AL 1537 -3.0 0.0 0.0 17.0 4.0 1742 1714 -28.0 0.0 0.0 0.0 76.0 1.0 584.0 3 0.0 0.0 0.0 0.0 0.0 3.0 0.0 3.0 30.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 13930.0, 0.0, 3.0, 10599.0, 30.0, 584.0, 1537.0)) 0 2019 1 1 5 null OO 13388 Mammoth Lakes, CA CA 14771 CA 1331 9.766090587178267 13.25822630939168 0.17428078149498794 18.331121368985617 7.59773267669035 1218 1484 4.257506232739596 13.65453925433288 0.18591674720785634 1.0 112.69446059194682 1.0 193.0 1 0.0 0.0 0.0 0.0 0.0 3.0 234.0 0.0 0.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 13388.0, 234.0, 0.0, 14771.0, 0.0, 193.0, 1331.0)) 1 2019 1 1 5 null OO 10140 Albuquerque, NM NM 12892 CA 1226 -5.0 0.0 0.0 12.0 6.0 1350 1330 -20.0 0.0 0.0 0.0 106.0 1.0 677.0 3 0.0 0.0 0.0 0.0 0.0 3.0 60.0 38.0 0.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 10140.0, 60.0, 38.0, 12892.0, 0.0, 677.0, 1226.0)) 0 2019 1 1 5 null OO 12892 Los Angeles, CA CA 14570 NV 2119 24.0 24.0 1.0 34.0 7.0 2244 2300 16.0 16.0 1.0 0.0 60.0 1.0 391.0 2 7.0 0.0 0.0 0.0 9.0 3.0 7.0 0.0 11.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 12892.0, 7.0, 0.0, 14570.0, 11.0, 391.0, 2119.0)) 1 2019 1 1 6 null OO 10693 Nashville, TN TN 11298 TX 626 -6.0 0.0 0.0 18.0 11.0 855 825 -30.0 0.0 0.0 0.0 90.0 1.0 631.0 3 0.0 0.0 0.0 0.0 0.0 3.0 26.0 18.0 1.0 Map(vectorType -> dense, length -> 9, values -> List(6.0, 3.0, 10693.0, 26.0, 18.0, 11298.0, 1.0, 631.0, 626.0)) 0 2019 1 1 6 null OO 11298 Dallas/Fort Worth, TX TX 14588 NM 855 -5.0 0.0 0.0 34.0 3.0 940 938 -2.0 0.0 0.0 0.0 66.0 1.0 435.0 2 0.0 0.0 0.0 0.0 0.0 3.0 3.0 1.0 38.0 Map(vectorType -> dense, length -> 9, values -> List(6.0, 3.0, 11298.0, 3.0, 1.0, 14588.0, 38.0, 435.0, 855.0)) 0 2019 1 1 6 null OO 11308 Dothan, AL AL 10397 GA 526 -4.0 0.0 0.0 10.0 4.0 735 716 -19.0 0.0 0.0 0.0 36.0 1.0 170

Here, we build the actual model using Logisitc Regression.

In [0]:
from pyspark.ml.classification import LogisticRegression

delLogReg = LogisticRegression(featuresCol="delayLikelyFeatures", labelCol="delayed?", predictionCol="predictionDelayed?")

delLogRegModel = delLogReg.fit(delayLikelyFinalPrep)

print("Coefficients: " + str(delLogRegModel.coefficients))
print("Intercept: " + str(delLogRegModel.intercept))

Coefficients: [0.009624060256547018,-0.020421837532772883,4.768256827701241e-06,-0.000399028286255554,-0.0013520831656750512,1.2090771136467725e-05,-0.003675846401250588,0.00013566184241600466,0.0008449014650474787]
Intercept: -2.117942295922091

After building the model, we can apply the predicted values to the database in new columns. The `predictionDelayed?` column shows which flights the model predicted to be delayed. In the `probability` column, the probability values can be seen. This value can be used as the likelihood of a flight being delayed.

In [0]:
finalDelayLikely = delLogRegModel.transform(delayLikelyFinalPrep)
display(finalDelayLikely)

Year Quarter Month DayofMonth FlightDate Reporting_Airline OriginAirportID OriginCityName OriginState DestAirportID DestState DepTime DepDelay DepDelayMinutes DepDel15 TaxiOut TaxiIn CRSArrTime ArrTime ArrDelay ArrDelayMinutes ArrDel15 Cancelled AirTime Flights Distance DistanceGroup CarrierDelay WeatherDelay NASDelay SecurityDelay LateAircraftDelay airlineIndex originCityIndex OriginStateIndex DestStateIndex delayLikelyFeatures delayed? rawPrediction probability predictionDelayed? 2019 1 1 4 null OO 10333 Alpena, MI MI 14150 MI 457 -7.0 0.0 0.0 16.0 4.0 604 542 -22.0 0.0 0.0 0.0 25.0 1.0 69.0 1 0.0 0.0 0.0 0.0 0.0 3.0 308.0 10.0 10.0 Map(vectorType -> dense, length -> 9, values -> List(4.0, 3.0, 10333.0, 308.0, 10.0, 14150.0, 10.0, 69.0, 457.0)) 0 Map(vectorType -> dense, length -> 2, values -> List(1.6980561292951313, -1.6980561292951313)) Map(vectorType -> dense, length -> 2, values -> List(0.8452806836712156, 0.15471931632878433)) 0.0 2019 1 1 4 null OO 14150 Pellston, MI MI 10333 MI 2231 -2.0 0.0 0.0 11.0 6.0 2336 2311 -25.0 0.0 0.0 0.0 23.0 1.0 69.0 1 0.0 0.0 0.0 0.0 0.0 3.0 259.0 10.0 10.0 Map(vectorType -> dense, length -> 9, values -> List(4.0, 3.0, 14150.0, 259.0, 10.0, 10333.0, 10.0, 69.0, 2231.0)) 0 Map(vectorType -> dense, length -> 2, values -> List(0.20759858139094356, -0.20759858139094356)) Map(vectorType -> dense, length -> 2, values -> List(0.5517140511742543, 0.4482859488257457)) 0.0 2019 1 1 5 null OO 14747 Seattle, WA WA 11638 CA 1927 -3.0 0.0 0.0 20.0 3.0 2141 2140 -1.0 0.0 0.0 0.0 110.0 1.0 748.0 3 0.0 0.0 0.0 0.0 0.0 3.0 17.0 15.0 0.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 14747.0, 17.0, 15.0, 11638.0, 0.0, 748.0, 1927.0)) 0 Map(vectorType -> dense, length -> 2, values -> List(0.21752217639116012, -0.21752217639116012)) Map(vectorType -> dense, length -> 2, values -> List(0.5541671318007548, 0.4458328681992452)) 0.0 2019 1 1 5 null OO 13486 Missoula, MT MT 14869 UT 1427 -3.0 0.0 0.0 10.0 8.0 1614 1601 -13.0 0.0 0.0 0.0 76.0 1.0 436.0 2 0.0 0.0 0.0 0.0 0.0 3.0 177.0 39.0 19.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 13486.0, 177.0, 39.0, 14869.0, 19.0, 436.0, 1427.0)) 0 Map(vectorType -> dense, length -> 2, values -> List(0.8153824974673483, -0.8153824974673483)) Map(vectorType -> dense, length -> 2, values -> List(0.6932552943390174, 0.3067447056609825)) 0.0 2019 1 1 5 null OO 14869 Salt Lake City, UT UT 10713 ID 830 0.0 0.0 0.0 35.0 3.0 1001 958 -3.0 0.0 0.0 0.0 50.0 1.0 290.0 2 0.0 0.0 0.0 0.0 0.0 3.0 18.0 19.0 37.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 14869.0, 18.0, 19.0, 10713.0, 37.0, 290.0, 830.0)) 0 Map(vectorType -> dense, length -> 2, values -> List(1.3589281211382551, -1.3589281211382551)) Map(vectorType -> dense, length -> 2, values -> List(0.7955854340882337, 0.20441456591176632)) 0.0 2019 1 1 5 null OO 11292 Denver, CO CO 11468 NE 2007 -3.0 0.0 0.0 19.0 5.0 2225 2213 -12.0 0.0 0.0 0.0 42.0 1.0 305.0 2 0.0 0.0 0.0 0.0 0.0 3.0 6.0 8.0 34.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 11292.0, 6.0, 8.0, 11468.0, 34.0, 305.0, 2007.0)) 0 Map(vectorType -> dense, length -> 2, values -> List(0.3396828981445428, -0.3396828981445428)) Map(vectorType -> dense, length -> 2, values -> List(0.584113493047676, 0.415886506952324)) 0.0 2019 1 1 5 null OO 13930 Chicago, IL IL 10599 AL 1537 -3.0 0.0 0.0 17.0 4.0 1742 1714 -28.0 0.0 0.0 0.0 76.0 1.0 584.0 3 0.0 0.0 0.0 0.0 0.0 3.0 0.0 3.0 30.0 Map(vectorType -> dense, length -> 9, values -> List(5.0, 3.0, 13930.0, 0.0, 3.0, 10599.0, 30.0, 584.0, 1537.0)) 0 Map(vectorType -> dense, length -> 2, values -> List(0.6730071801379962, -0.6730071801379962)) Map(vectorType -> dense, length -> 2, values -> List(0.6621761897673373, 0.33782381023266267)) 0.0 2019 1 1 5 null OO 13388 Mammoth Lakes, CA CA 14771 CA 1331 9.766090587178267 13.25822630939168 0.17428078149498794 18.331121368985617 7.59773267669035 1218 1484 4.257506232739596 13.65453925433288 0.18591674720785634 1.0 112.69

In [0]:
finalDelayLikely = finalDelayLikely.withColumn("equal?", col("predictionDelayed?") == col("delayed?"))
display(finalDelayLikely.groupBy('equal?').count())

equal? count true 382187 false 201796

Here we can see that the model was correct 382187 times out of 583983, meaning the model was correct 65.4% of the time.

#####2.4.3 Predicting Departure Delay length (Using Linear Regression)

Next, we will build a model that predicts how long of a delay a flight will have. Because we are now predicting a specific value, we will be using Linear Regression. We use the same columns of the database for this model, as we did for the features of the logistical regression model. The null values were most often there because the flight was canelled. But here, we will use the Departure Delay column as the label column, and attempt to predict this information using our feature columns.

In [0]:
delayFeatureCols = ["DayofMonth", "airlineIndex", "OriginAirportID", "originCityIndex", "OriginStateIndex", "DestAirportID", "DestStateIndex", "Distance", "DepTime"]

assembler = (VectorAssembler()
  .setInputCols(delayFeatureCols)
  .setOutputCol("delayFeatures"))

delayFinalPrep = assembler.transform(indexedData)

In [0]:
from pyspark.ml.regression import LinearRegression

lr = LinearRegression(featuresCol="delayFeatures", labelCol="DepDelay", predictionCol="predictionDepDelay")

lrModel = lr.fit(delayFinalPrep)

print("Coefficients: %s" % str(lrModel.coefficients))
print("Intercept: %s" % str(lrModel.intercept))

trainingSummary = lrModel.summary
trainingSummary.residuals.show()
print("RMSE: %f" % trainingSummary.rootMeanSquaredError)
print("r2: %f" % trainingSummary.r2)


Coefficients: [0.2112551913904861,0.16255305140588233,0.00020531928387665743,0.006305683723620622,0.01713387001713886,0.00018359468355235673,-0.05821605428917896,0.0009275406908679112,0.01178356486704429]
Intercept: -15.478074864285457
+-------------------+
 residuals|
+-------------------+
 -4.554452184121361|
 -20.23244055523838|
-17.995313262518195|
 -12.46244218373069|
 0.5800000076073193|
-15.617863246917615|
 -10.82982086774787|
 0.9010685143004142|
 -11.6187241045333|
 7.876383453739091|
 -4.922778441083565|
 -4.577360971224971|
-2.5508562164838917|
-5.7287987904941815|
 -3.966597790764755|
 1.2903852403943432|
-13.142215821428824|
-0.8647609984495972|
-28.638940302872726|
-12.528734664337964|
+-------------------+
only showing top 20 rows

RMSE: 47.556036
r2: 0.016005

In [0]:
finalDepDelay = lrModel.transform(delayFinalPrep)

Here we can see the values our model predicted in the `predicitonDepDelay` column (The original values are in the column `DepDelay`). These are the times (in minutes) the model predicted a flight to be delayed by during departure.

In [0]:
finalDepDelay.select("Reporting_Airline", "OriginCityName", "DestState", "DepDelay", "predictionDepDelay").show()

+-----------------+--------------------+---------+-----------------+-------------------+
Reporting_Airline| OriginCityName|DestState| DepDelay| predictionDepDelay|
+-----------------+--------------------+---------+-----------------+-------------------+
 OO| Alpena, MI| MI| -7.0| -2.445547815878639|
 OO| Pellston, MI| MI| -2.0| 18.23244055523838|
 OO| Seattle, WA| CA| -3.0| 14.995313262518195|
 OO| Missoula, MT| UT| -3.0| 9.46244218373069|
 OO| Salt Lake City, UT| ID| 0.0|-0.5800000076073193|
 OO| Denver, CO| NE| -3.0| 12.617863246917615|
 OO| Chicago, IL| AL| -3.0| 7.82982086774787|
 OO| Mammoth Lakes, CA| CA|9.766090587178267| 8.865022072877853|
 OO| Albuquerque, NM| CA| -5.0| 6.6187241045333|
 OO| Los Angeles, CA| NV| 24.0| 16.12361654626091|
 OO| Nashville, TN| TX| -6.0|-1.0772215589164347|
 OO|Dallas/Fort Worth...| NM| -5.0|-0.4226390287750288|
 OO| Dothan, AL| GA| -4.0|-1.4491437835161083|
 OO| Fort Wayne, IN| GA| -5.0| 0.7287987904941815|
 OO| Salt Lake City, UT| MT| 11.0| 14.966597790764755|
 OO| Salt Lake City, UT| TX| 11.0| 9.709614759605657|
 OO| Idaho Falls, ID| UT| 1.0| 14.142215821428824|
 OO| Salt Lake City, UT| ID| 5.0| 5.864760998449597|
 OO| Lafayette, LA| GA| -16.0| 12.638940302872726|
 OO| Los Angeles, CA| TX| 1.0| 13.528734664337964|
+-----------------+--------------------+---------+-----------------+-------------------+
only showing top 20 rows

#####2.4.4 Predicting likelihood of a Flight being cancelled (Using Binomial Logistic Regression)

Next, we will move on to building a model that predicts cancelled flights. This model will use Logistic Regression because it is predicting a binary result. It will again use the same set of feature columns used in the above models, minus the departure time column because during the cleaning of the data this column was filled with the average value if a row had a null values.

In [0]:
cancelLiklyFeatureCols = ["DayofMonth", "airlineIndex", "OriginAirportID", "originCityIndex", "OriginStateIndex", "DestAirportID", "DestStateIndex", "Distance"]

assembler = (VectorAssembler()
  .setInputCols(cancelLiklyFeatureCols)
  .setOutputCol("cancelLikelyFeatures"))

cancelLikelyFinalPrep = assembler.transform(indexedData)


This time there is already a `Cancelled` column that has the information we need for it to be the label column that we will then predict.

In [0]:
canLogReg = LogisticRegression(featuresCol="cancelLikelyFeatures", labelCol="Cancelled", predictionCol="predictionCancelled?")

canLogRegModel = canLogReg.fit(cancelLikelyFinalPrep)

print("Coefficients: " + str(canLogRegModel.coefficients))
print("Intercept: " + str(canLogRegModel.intercept))

Coefficients: [0.08429767216215427,0.001988688430627684,6.824259494684082e-05,0.000501872394976121,0.0034670484784176323,6.857916792093917e-05,0.0016928799293790147,-0.0006432345952401548]
Intercept: -6.489165987575349

In [0]:
finalCancelLikely = canLogRegModel.transform(cancelLikelyFinalPrep)
display(finalCancelLikely)

Year Quarter Month DayofMonth FlightDate Reporting_Airline OriginAirportID OriginCityName OriginState DestAirportID DestState DepTime DepDelay DepDelayMinutes DepDel15 TaxiOut TaxiIn CRSArrTime ArrTime ArrDelay ArrDelayMinutes ArrDel15 Cancelled AirTime Flights Distance DistanceGroup CarrierDelay WeatherDelay NASDelay SecurityDelay LateAircraftDelay airlineIndex originCityIndex OriginStateIndex DestStateIndex cancelLikelyFeatures rawPrediction probability predictionCancelled? 2019 1 1 4 null OO 10333 Alpena, MI MI 14150 MI 457 -7.0 0.0 0.0 16.0 4.0 604 542 -22.0 0.0 0.0 0.0 25.0 1.0 69.0 1 0.0 0.0 0.0 0.0 0.0 3.0 308.0 10.0 10.0 Map(vectorType -> dense, length -> 8, values -> List(4.0, 3.0, 10333.0, 308.0, 10.0, 14150.0, 10.0, 69.0)) Map(vectorType -> dense, length -> 2, values -> List(4.308670479308812, -4.308670479308812)) Map(vectorType -> dense, length -> 2, values -> List(0.9867271174848887, 0.01327288251511128)) 0.0 2019 1 1 4 null OO 14150 Pellston, MI MI 10333 MI 2231 -2.0 0.0 0.0 11.0 6.0 2336 2311 -25.0 0.0 0.0 0.0 23.0 1.0 69.0 1 0.0 0.0 0.0 0.0 0.0 3.0 259.0 10.0 10.0 Map(vectorType -> dense, length -> 8, values -> List(4.0, 3.0, 14150.0, 259.0, 10.0, 10333.0, 10.0, 69.0)) Map(vectorType -> dense, length -> 2, values -> List(4.334546925704776, -4.334546925704776)) Map(vectorType -> dense, length -> 2, values -> List(0.9870617802064128, 0.012938219793587273)) 0.0 2019 1 1 5 null OO 14747 Seattle, WA WA 11638 CA 1927 -3.0 0.0 0.0 20.0 3.0 2141 2140 -1.0 0.0 0.0 0.0 110.0 1.0 748.0 3 0.0 0.0 0.0 0.0 0.0 3.0 17.0 15.0 0.0 Map(vectorType -> dense, length -> 8, values -> List(5.0, 3.0, 14747.0, 17.0, 15.0, 11638.0, 0.0, 748.0)) Map(vectorType -> dense, length -> 2, values -> List(4.677815576876521, -4.677815576876521)) Map(vectorType -> dense, length -> 2, values -> List(0.9907863749782635, 0.009213625021736454)) 0.0 2019 1 1 5 null OO 13486 Missoula, MT MT 14869 UT 1427 -3.0 0.0 0.0 10.0 8.0 1614 1601 -13.0 0.0 0.0 0.0 76.0 1.0 436.0 2 0.0 0.0 0.0 0.0 0.0 3.0 177.0 39.0 19.0 Map(vectorType -> dense, length -> 8, values -> List(5.0, 3.0, 13486.0, 177.0, 39.0, 14869.0, 19.0, 436.0)) Map(vectorType -> dense, length -> 2, values -> List(4.1459275385006, -4.1459275385006)) Map(vectorType -> dense, length -> 2, values -> List(0.984417897791652, 0.015582102208347973)) 0.0 2019 1 1 5 null OO 14869 Salt Lake City, UT UT 10713 ID 830 0.0 0.0 0.0 35.0 3.0 1001 958 -3.0 0.0 0.0 0.0 50.0 1.0 290.0 2 0.0 0.0 0.0 0.0 0.0 3.0 18.0 19.0 37.0 Map(vectorType -> dense, length -> 8, values -> List(5.0, 3.0, 14869.0, 18.0, 19.0, 10713.0, 37.0, 290.0)) Map(vectorType -> dense, length -> 2, values -> List(4.361317642304213, -4.361317642304213)) Map(vectorType -> dense, length -> 2, values -> List(0.9873992439288868, 0.012600756071113337)) 0.0 2019 1 1 5 null OO 11292 Denver, CO CO 11468 NE 2007 -3.0 0.0 0.0 19.0 5.0 2225 2213 -12.0 0.0 0.0 0.0 42.0 1.0 305.0 2 0.0 0.0 0.0 0.0 0.0 3.0 6.0 8.0 34.0 Map(vectorType -> dense, length -> 8, values -> List(5.0, 3.0, 11292.0, 6.0, 8.0, 11468.0, 34.0, 305.0)) Map(vectorType -> dense, length -> 2, values -> List(4.612531293367801, -4.612531293367801)) Map(vectorType -> dense, length -> 2, values -> List(0.9901709108262438, 0.0098290891737562)) 0.0 2019 1 1 5 null OO 13930 Chicago, IL IL 10599 AL 1537 -3.0 0.0 0.0 17.0 4.0 1742 1714 -28.0 0.0 0.0 0.0 76.0 1.0 584.0 3 0.0 0.0 0.0 0.0 0.0 3.0 0.0 3.0 30.0 Map(vectorType -> dense, length -> 8, values -> List(5.0, 3.0, 13930.0, 0.0, 3.0, 10599.0, 30.0, 584.0)) Map(vectorType -> dense, length -> 2, values -> List(4.698683073372795, -4.698683073372795)) Map(vectorType -> dense, length -> 2, values -> List(0.9909749308716759, 0.009025069128324051)) 0.0 2019 1 1 5 null OO 13388 Mammoth Lakes, CA CA 14771 CA 1331 9.766090587178267 13.25822630939168 0.17428078149498794 18.331121368985617 7.59773267669035 1218 1484 4.257506232739596 13.65453925433288 0.18591674720785634 1.0 112.69446059194682 1.0 193.0 1 0.0 0.0 0.0 0.0 0.0 3.0 234.0 0.0 0.0 Map(vectorType -> dense,

In [0]:
display(finalCancelLikely.groupBy('predictionCancelled?').count())

predictionCancelled? count 0.0 583983

This model unfortunately did not predict whether a flight will be cancelled, always predicting a flight will not be cancelled. This could be for a few different reasons. There was a very small amount of flights that were cancelled and there may not be enough patterns in our dataset to predict cancellations. It might also be possible that cancellations are not predictable using the chosen Logistic Regression model.

##### 2.4.5 Predicting Cancelled Flights With a Random Forest Classifier

Since the logistic model was unable to classify whether or not a flight would be cancelled, the Random Forest Regression model was considered. Using various depths and number of decision trees, a model was constructed.  For this model, the indexed data was split into a training and test set, with 70% of the data going to the training data, and 30% being used for testing the model.

In [0]:
from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.tuning import ParamGridBuilder, TrainValidationSplit
from pyspark.ml.evaluation import RegressionEvaluator

from pyspark.ml import Pipeline


trainingCancel, testCancel = cancelLikelyFinalPrep.randomSplit([0.7, 0.3])

trainingCancel.cache()
testCancel.cache()

rfModel = (RandomForestRegressor()
  .setLabelCol("Cancelled")
  .setFeaturesCol("cancelLikelyFeatures"))

paramGrid = (ParamGridBuilder()
  .addGrid(rfModel.maxBins, [340]) # so that we can consider all the unique values in a column
  .addGrid(rfModel.maxDepth, [2, 4, 6])
  .addGrid(rfModel.numTrees, [10, 15, 30])
  .build())


stages = [rfModel]

pipeline = Pipeline().setStages(stages)


tvs = (TrainValidationSplit() 
  .setEstimator(pipeline) 
  .setEstimatorParamMaps(paramGrid)
  .setEvaluator(RegressionEvaluator().setLabelCol("Cancelled")))

pipelineFitted = tvs.fit(trainingCancel)

/databricks/spark/python/pyspark/ml/util.py:762: UserWarning: Cannot find mlflow module. To enable MLflow logging, install mlflow from PyPI.
 warnings.warn(_MLflowInstrumentation._NO_MLFLOW_WARNING)

After building the model and fitting it to the training data with various hyperpameters, it is time to examine the performance of the fitted pipeline.

In [0]:
print("The Best Parameters:\n--------------------")
print(pipelineFitted.bestModel.stages[0])
pipelineFitted.bestModel.stages[0].extractParamMap()

The Best Parameters:
--------------------
RandomForestRegressionModel: uid=RandomForestRegressor_43c2861de370, numTrees=10, numFeatures=8
Out[36]: {Param(parent='RandomForestRegressor_43c2861de370', name='bootstrap', doc='Whether bootstrap samples are used when building trees.'): True,
 Param(parent='RandomForestRegressor_43c2861de370', name='cacheNodeIds', doc='If false, the algorithm will pass trees to executors to match instances with nodes. If true, the algorithm will cache node IDs for each instance. Caching can speed up training of deeper trees. Users can set how often should the cache be checkpointed or disable it by setting checkpointInterval.'): False,
 Param(parent='RandomForestRegressor_43c2861de370', name='checkpointInterval', doc='set checkpoint interval (>= 1) or disable checkpoint (-1). E.g. 10 means that the cache will get checkpointed every 10 iterations. Note: this setting will be ignored if the checkpoint directory is not set in the SparkContext.'): 10,
 Param(parent='RandomForestRegressor_43c2861de370', name='featureSubsetStrategy', doc="The number of features to consider for splits at each tree node. Supported options: 'auto' (choose automatically for task: If numTrees == 1, set to 'all'. If numTrees > 1 (forest), set to 'sqrt' for classification and to 'onethird' for regression), 'all' (use all features), 'onethird' (use 1/3 of the features), 'sqrt' (use sqrt(number of features)), 'log2' (use log2(number of features)), 'n' (when n is in the range (0, 1.0], use n * number of features. When n is in the range (1, number of features), use n features). default = 'auto'"): 'auto',
 Param(parent='RandomForestRegressor_43c2861de370', name='featuresCol', doc='features column name.'): 'cancelLikelyFeatures',
 Param(parent='RandomForestRegressor_43c2861de370', name='impurity', doc='Criterion used for information gain calculation (case-insensitive). Supported options: variance'): 'variance',
 Param(parent='RandomForestRegressor_43c2861de370', name='labelCol', doc='label column name.'): 'Cancelled',
 Param(parent='RandomForestRegressor_43c2861de370', name='leafCol', doc='Leaf indices column name. Predicted leaf index of each instance in each tree by preorder.'): '',
 Param(parent='RandomForestRegressor_43c2861de370', name='maxBins', doc='Max number of bins for discretizing continuous features. Must be >=2 and >= number of categories for any categorical feature.'): 340,
 Param(parent='RandomForestRegressor_43c2861de370', name='maxDepth', doc='Maximum depth of the tree. (>= 0) E.g., depth 0 means 1 leaf node; depth 1 means 1 internal node + 2 leaf nodes.'): 6,
 Param(parent='RandomForestRegressor_43c2861de370', name='maxMemoryInMB', doc='Maximum memory in MB allocated to histogram aggregation. If too small, then 1 node will be split per iteration, and its aggregates may exceed this size.'): 256,
 Param(parent='RandomForestRegressor_43c2861de370', name='minInfoGain', doc='Minimum information gain for a split to be considered at a tree node.'): 0.0,
 Param(parent='RandomForestRegressor_43c2861de370', name='minInstancesPerNode', doc='Minimum number of instances each child must have after split. If a split causes the left or right child to have fewer than minInstancesPerNode, the split will be discarded as invalid. Should be >= 1.'): 1,
 Param(parent='RandomForestRegressor_43c2861de370', name='minWeightFractionPerNode', doc='Minimum fraction of the weighted sample count that each child must have after split. If a split causes the fraction of the total weight in the left or right child to be less than minWeightFractionPerNode, the split will be discarded as invalid. Should be in interval [0.0, 0.5).'): 0.0,
 Param(parent='RandomForestRegressor_43c2861de370', name='numTrees', doc='Number of trees to train (>= 1).'): 10,
 Param(parent='RandomForestRegressor_43c2861de370', name='predictionCol', doc='prediction column name.'): 'prediction',
 Param(parent='RandomForestRegressor_43c2861de370', name='seed', doc='random seed.'): 250

It seems that the best hyperparameters for this Random Forest Model was 15 trees and 8 features.

In [0]:
results = (pipelineFitted.bestModel
  .transform(testCancel)
  .selectExpr("prediction as raw_prediction", 
    "double(round(prediction)) as prediction", 
    "Cancelled", 
    """CASE double(round(prediction)) = Cancelled
  WHEN true then 1
  ELSE 0
END as equal"""))

display(results.selectExpr("sum(equal)/sum(1)"))

(sum(equal) / sum(1)) 0.9735096313043081

From the results here it seems like a very large amount of the entries (about 97.4%) were classified properly in the test set. The Random Forest Model was very accurate at determining whether or not the flight would be cancelled.

In [0]:
totalResults = (pipelineFitted.bestModel
  .transform(cancelLikelyFinalPrep)
  .selectExpr("prediction as raw_prediction", 
    "double(round(prediction)) as prediction", 
    "Cancelled", 
    """CASE double(round(prediction)) = Cancelled
  WHEN true then 1
  ELSE 0
END as equal"""))

display(totalResults.selectExpr("sum(equal)/sum(1)"))

(sum(equal) / sum(1)) 0.9740626011373619

For the dataset with filtered entries, the Random Forest Model was able to predict whether or not a given flight would be cancelled with accuracy of 97.406%.

#### 3. Conclusion